# CptS 481 - Python Software Construction

## Unit 11: Builtins

In [1]:
from IPython.display import HTML
HTML(open("notes.css", "r").read())

In [2]:
allowExceptions = False # enable to allow interruption of Jupyter "Restart"

### The ``math`` and ``cmath`` Modules

The ``math`` module provides all of the basic math functions in the C ``math(3)`` library.

In [3]:
from math import * # a good time to use "import *"

headerFormat = "{:10} {:10} {:10} {:10} {:10} {:10}"
dataFormat   = "{:10.3f} {:10.3f} {:10.3f} {:10.3g} {:10.5f} {:10.5f}"
print(headerFormat.format("     x",    "    sin(x)", "    cos(x)",
                          "    tan(x)", "    exp(x)", "    exp(-x)"))
for i in range(17):
    x = 2*pi*i/16
    print(dataFormat.format(x, sin(x), cos(x), tan(x), exp(x), exp(-x)))

     x         sin(x)     cos(x)     tan(x)     exp(x)     exp(-x)
     0.000      0.000      1.000          0    1.00000    1.00000
     0.393      0.383      0.924      0.414    1.48097    0.67523
     0.785      0.707      0.707          1    2.19328    0.45594
     1.178      0.924      0.383       2.41    3.24819    0.30786
     1.571      1.000      0.000   1.63e+16    4.81048    0.20788
     1.963      0.924     -0.383      -2.41    7.12419    0.14037
     2.356      0.707     -0.707         -1   10.55072    0.09478
     2.749      0.383     -0.924     -0.414   15.62533    0.06400
     3.142      0.000     -1.000  -1.22e-16   23.14069    0.04321
     3.534     -0.383     -0.924      0.414   34.27073    0.02918
     3.927     -0.707     -0.707          1   50.75402    0.01970
     4.320     -0.924     -0.383       2.41   75.16532    0.01330
     4.712     -1.000     -0.000   5.44e+15  111.31778    0.00898
     5.105     -0.924      0.383      -2.41  164.85859    0.00607
     5.49

This works with floats, but not with complex:

In [4]:
if allowExceptions:
    sqrt(-1)

In [5]:
if allowExceptions:
    exp(1j)

So you use the ``cmath`` module:

In [6]:
from cmath import *

print(sqrt(-1))

1j


In [7]:
(-1)**0.5 # exponentiation allows complex, even when sqrt() is math.sqrt()

(6.123233995736766e-17+1j)

In [8]:
print(exp(1j))

(0.5403023058681398+0.8414709848078965j)


### Random Numbers: The random Module

#### Pseudorandom Numbers: The random.Random Class

This is an interface to the standard ``random(3)`` pseudorandom library. Instances of the ``Random`` class are random number generators (in the Python sense), but there's a global generator ``Random.random()``.

There are lots of random distributions possible:

In [9]:
import random
?random

In [10]:
rng0 = random.Random()
random.Random.random(rng0)

0.8615304352787039

In [11]:
for i in range(10):
    print(random.random())

0.05187948347388738
0.6337459238174988
0.17238948176814062
0.7723058280026973
0.01778783831582198
0.46466416396044796
0.6318908688996867
0.9620503624806558
0.19845727428023463
0.02480615070738279


In [12]:
seq = [ 1, "spam", 3.4 ]
random.choice(seq)

'spam'

In [13]:
rolls = range(1, 7)
random.choice(rolls)

6

In [14]:
random.shuffle(seq)
seq

[3.4, 'spam', 1]

In [15]:
l = list("python")
random.shuffle(l)
"".join(l)

'nohpyt'

In [16]:
for i in range(10):
    print(random.gauss(mu=0, sigma=1))

0.16912466900954132
1.7823121496918009
0.09894423486781453
0.2541951290268671
1.0740449255596698
0.3567048932099403
-2.3476246355562234
0.9046055194753334
-0.37612097702665503
-0.4589444209821537


In [17]:
# How long and how many calls does it take a Gaussian random number
# generator to generate a value that exceeds 5 standard deviations?

from time import time

ct = 1
startTime = time()
while True:
    r = random.gauss(0, 1)
    if abs(r) > 5: # 6 would be nice, but takes a long time
        break
    ct += 1

print("generated value:", r)
print("          calls:", ct)
print("   elapsed time: {:.3f}s".format(time() - startTime))

generated value: 5.11633334708242
          calls: 694730
   elapsed time: 0.705s


#### True Random Numbers: The ``random.SystemRandom`` Class

This is an interface to the ``random(4)`` *really* (not pseudo) random device.

When should you use this?

In [18]:
rng = random.SystemRandom()
random.SystemRandom.random(rng)

0.344670204881647

#### Example of Random Number Usage: ``markov``

Markov generation works like this:

Given a text

In [19]:
text = r"""
old mac donald had a farm
e i e i o
and on this farm he had some ducks
e i e i o
with a quack quack here
and a quack quack there
here a quack
there a quack
everywhere a quack quack
old mac donald had a farm
e i e i o
"""

Split the text into words:

In [20]:
words = text.split()
if 1:
    print(words)

['old', 'mac', 'donald', 'had', 'a', 'farm', 'e', 'i', 'e', 'i', 'o', 'and', 'on', 'this', 'farm', 'he', 'had', 'some', 'ducks', 'e', 'i', 'e', 'i', 'o', 'with', 'a', 'quack', 'quack', 'here', 'and', 'a', 'quack', 'quack', 'there', 'here', 'a', 'quack', 'there', 'a', 'quack', 'everywhere', 'a', 'quack', 'quack', 'old', 'mac', 'donald', 'had', 'a', 'farm', 'e', 'i', 'e', 'i', 'o']


To generate the Markov text, start with an empty dictionary representing a table, then go though every word in ``words`` and build a table (dictionary) that matches each successive pair of words to a list of their successors:

In [21]:
import random
from pprint import pprint

def buildMarkovTable(words):
    nonword = '\n'

    word1 = nonword
    word2 = nonword

    table = { }
    for word in words:
        # add (word1, word2): word to the table
        if (word1, word2) in table:
            table[word1, word2].append(word)
        else:
            table[word1, word2] = [ word ]
        word1, word2 = word2, word

    # Mark the end of the file
    table.setdefault( (word1, word2), [] ).append(nonword)

    return table

table = buildMarkovTable(words)
if 1:
    pprint(table)

{('\n', '\n'): ['old'],
 ('\n', 'old'): ['mac'],
 ('a', 'farm'): ['e', 'e'],
 ('a', 'quack'): ['quack', 'quack', 'there', 'everywhere', 'quack'],
 ('and', 'a'): ['quack'],
 ('and', 'on'): ['this'],
 ('donald', 'had'): ['a', 'a'],
 ('ducks', 'e'): ['i'],
 ('e', 'i'): ['e', 'o', 'e', 'o', 'e', 'o'],
 ('everywhere', 'a'): ['quack'],
 ('farm', 'e'): ['i', 'i'],
 ('farm', 'he'): ['had'],
 ('had', 'a'): ['farm', 'farm'],
 ('had', 'some'): ['ducks'],
 ('he', 'had'): ['some'],
 ('here', 'a'): ['quack'],
 ('here', 'and'): ['a'],
 ('i', 'e'): ['i', 'i', 'i'],
 ('i', 'o'): ['and', 'with', '\n'],
 ('mac', 'donald'): ['had', 'had'],
 ('o', 'and'): ['on'],
 ('o', 'with'): ['a'],
 ('old', 'mac'): ['donald', 'donald'],
 ('on', 'this'): ['farm'],
 ('quack', 'everywhere'): ['a'],
 ('quack', 'here'): ['and'],
 ('quack', 'old'): ['mac'],
 ('quack', 'quack'): ['here', 'there', 'old'],
 ('quack', 'there'): ['here', 'a'],
 ('some', 'ducks'): ['e'],
 ('there', 'a'): ['quack'],
 ('there', 'here'): ['a'],
 ('th

Now, generate the output text.

In [22]:
def printMarkovText(table, words):
    nonword = '\n'

    maxwords = 10000 # limit the maximum number of words
    maxwidth = 60

    word1 = nonword
    word2 = nonword

    line = ""
    for i in range(maxwords):
        newword = random.choice(table[(word1, word2)])
        if newword == nonword:
            break
        if len(line) + 1 + len(newword) > maxwidth:
            print(line)
            line = ""
        line += newword + " "
        word1, word2 = word2, newword

    if line != "": # flush out the last blank line, if any
        print(line)

printMarkovText(table, words)

old mac donald had a farm e i o and on this farm he had 
some ducks e i o 


Now let's try this on some longer, more interesting texts:

In [23]:
%%sh
ls texts

1ws1711.txt
galileo.txt
kiplingbio.txt
pg8164.txt


In [24]:
def printMarkovFile(fileName):
    text = open(fileName).read()
    words = text.split()
    table = buildMarkovTable(words)
    printMarkovText(table, words)

Here are Markov versions of a biography of Galileo ...

In [25]:
printMarkovFile("texts/galileo.txt")

Galileo Galilei was an Italian physicist, mathematician, 
astronomer, and philosopher who played a major role in the 
Scientific Revolution. His achievements include 
improvements to the absence of an observed stellar 
parallax. The matter was investigated by the Inquisition, 
found "vehemently suspect of heresy", forced to recant, and 
spent the rest of his finest works, Two New Sciences, in 
which he summarised the work he had done some forty years 
earlier, on the two sciences now called kinematics and 
strength of materials. 


... a biography of Rudyard Kipling ...

In [26]:
printMarkovFile("texts/kiplingbio.txt")

Kipling gained renown throughout the world as a poet and 
storyteller. He was also known as a poet and storyteller. 
He was also known as a leading supporter of the Indian 
People, as seen through the eyes of the courage of an 
Indian boy who is shot while carrying water to British 
soldiers in the thick of battle. Mandalay tries to capture 
the strange atmosphere of the animals who can talk. The 
stories of Mowgli, a man-cub who was the duty of Great 
Britain to carry the white man's burden by civilizing 
backward races. But he was 12, poor health kept him from 
attending. At 17, Kipling returned to England from the 
United States. Writing Poems Kipling composed many of his 
views toward empire, which many misunderstood. In many of 
his works, Kipling seemed to imply that it was the central 
character in The Jungle Book, brought Kipling great 
popularity in England and the United States. Writing Poems 
Kipling composed many of his highly popular works. 


... Shakespeare's "A Midsummer Night's Dream" ...

In [27]:
printMarkovFile("texts/1ws1711.txt")

The Complete Works of William Shakespeare DRAMATIS PERSONAE 
THESEUS, Duke of Athens yields you up- Which by no means we 
may rehearse most obscenely and courageously. Take pains; 
be perfect; adieu. QUINCE. At the Duke's oak we meet. 
BOTTOM. Enough; hold, or cut bow-strings. Exeunt <<THIS 
ELECTRONIC VERSION OF THE COMPLETE WORKS OF WILLIAM 
SHAKESPEARE IS COPYRIGHT 1990-1993 BY WORLD LIBRARY, INC., 
AND IS PROVIDED BY PROJECT GUTENBERG ETEXT OF CARNEGIE 
MELLON UNIVERSITY WITH PERMISSION. ELECTRONIC AND MACHINE 
READABLE COPIES MAY BE DISTRIBUTED SO LONG AS SUCH COPIES 
(1) ARE FOR YOUR OR OTHERS PERSONAL USE ONLY, AND (2) ARE 
NOT DISTRIBUTED OR USED COMMERCIALLY. PROHIBITED COMMERCIAL 
DISTRIBUTION INCLUDES BY ANY SERVICE THAT CHARGES FOR 
DOWNLOAD TIME OR FOR MEMBERSHIP.>> ACT II. SCENE I. The 
wood. TITANIA lying asleep Enter QUINCE, FLUTE, SNOUT, and 
STARVELING QUINCE. Have you come by night, Full often hath 
she gossip'd by my life! And never did I hear Such gallant 
chiding,

in the world; Unless you can find sport in their mirth, and 
neeze, and swear A merrier hour was never wasted there. But 
room, fairy, here comes Oberon. FAIRY. And here the maiden, 
sleeping sound, On the ground Sleep sound; I'll apply To 
your eye, My tongue should catch your tongue's sweet 
melody. Were the world That hatred is so oft beguil'd. As 
waggish boys in game themselves forswear, So the boy Love 
is perjur'd everywhere; For ere Demetrius look'd on 
Hermia's eyes, So I, admiring of his qualities. Things base 
and vile, holding no quantity, Love can transpose to form 
and dignity. Love looks not with some care, that he heard, 
and is to make me afeard. Re-enter SNOUT SNOUT. O Bottom, 
thou art beautiful. BOTTOM. Not a mouse Shall disturb this 
hallowed house. I am not guilty of Lysander's blood; Nor is 
he dead, for aught that I should know the man By the dead 
and drowsy fire; Every elf and fairy sprite Hop as light as 
tales. LYSANDER. I will condole in some measure. To th

shun me, and I am to entreat you, request you, and a 
lantern, and say he comes to disfigure or to abjure For 
ever the society of men. Therefore, fair Hermia, look you 
arm yourself To fit your fancies to your father's choice, 
You can play no part but Pyramus; for Pyramus is not 
friendly, 'tis not maidenly; Our sex, as well deriv'd as 
he, As well possess'd; my love do dwell, That he awaking 
when the next new moon- The sealing-day betwixt my love and 
courtesy Lie further off yet; do not lie so near. LYSANDER. 
O, take the sense, sweet, of my innocence! Love takes the 
meaning in love's conference. I mean that my heart unto 
yours is knit, So that but one heart we can make of it; Two 
bosoms interchained with an ass's head BOTTOM. If I have 
had a most rare vision. I have a reasonable good ear in 
music. Let's have the child of me. His mother was a 
vot'ress of my spirit; For I upon this bank will rest me. 
[Lies down] Come, thou gentle day. For if but once thou 
show me thy chink,

... and P. J. Wodehouse's "My Man Jeeves".

In [28]:
printMarkovFile("texts/pg8164.txt")

﻿MY MAN JEEVES BY P. G. Wodehouse *** END OF THIS PROJECT 
GUTENBERG EBOOK MY MAN JEEVES *** ***** This and all that; 
and the refreshing sleep. We had just come from seeing dear 
old chap in a general sort of girl you love, Reggie?" 
"Never. I've been reading about in the time. "Well, it's 
only sometimes. I can't remember what it was a girl. He had 
to sit and listen to a degree. You're sitting in the 
afternoon." "So he did, Jeeves; so he did," I said, to 
cheer him up. "What's the trouble? Anything up?" "I've 
finished the castle he seemed to me to other copies of the 
hippodrome. Presently the others began to get him in hand 
at all, except perhaps an occasional poem recommending the 
young lady asks to be done to divert her mind. She's 
brooding about something. She's been like that for the poor 
old Freddie had his strong qualities. He was what American 
chappies would call a Theosophist, and he subsided. Poor 
old Freddie that to know the truth. "I'm awfully sorry, you 
know," 

knows that it's funny I _hadn't_ noticed it. "Is that the 
auditorium was full of merriment and good cheer, and I was 
just going to let Jeeves treat me like a lost child who 
spots his father in the old boy instead of in Colorado?" 
Bicky rocked like a lost child who made me feel as if they 
thought there was a time when the visitor appeared. He was 
what put the lantern I had sucked down a whole lot. A 
pretty hot brain-wave; and that's all there was more 
remarkable for the next few days made in dear old Freddie 
seemed to have someone to talk on the half-size billiard 
table with the aid of the right sort, some who rolled in 
dollars in houses up by the way she looked a bit here, and 
is sick, as if he hadn't got to do it as a jolly little 
party it was--not. I'm no Bombardier Wells myself, but I 
have always wished to do. I want you to select according to 
your aunt." "I might--if I wanted him to be dragged home 
with ropes. It must have missed him. My name's Wooster, 
don't you k

that explained why he had gone to bed. I felt I wanted a 
bit thick. If it hadn't seemed quite so bad from there. 
"Well?" said Freddie, when silence had set my heart on the 
version I had rather a foggy recollection of that quiet 
little domestic evening bucked him up on my evening clothes 
have I?" "We have three suits full of life. But then 
Rocky's letters, based on sound foundations. No doubt you 
are outside the United States. 1.E. Unless you get the kid 
undressed had been rather difficult to restore a child who 
spots his father in the bathroom. It hurt her--my being 
there. At this point I fell asleep again. I was glad to see 
Mr. Lattaker? Still hard at it?" "He is an agreeable 
gentleman, but not limited to, incomplete, inaccurate or 
corrupt data, transcription errors, a copyright notice is 
included. Thus, we do about it?" "We can't spend our time 
acting as nurses to this--this exhibit." He got quite 
excited. Said that if this was marriage, I thought, when I 
came to me 

### Invoking the Python Interpreter ###

#### The ``eval()`` Function ####

This function will evaluate *expressions*. They may be in the form of a string:

In [44]:
x = 4
result = eval("x ** 2")
print(result)

16


If you pass a second argument, it will be used as the namespace used for the evaluation:

In [50]:
x = 4
result = eval("x ** 2", {'x': 6})
print(result)

36


In [48]:
?eval

#### The ``compile()`` Function ####

The ``compile()`` function turns a string into a compiled object that may be passed to ``eval()`` or (below) ``exec()``. The syntax is;

    compile(source, fileName, mode, ... )

``source`` is a string. ``fileName`` is what you want to pretend the source file is (for error messages), and ``mode`` is ``"exec"`` (treat the string as a module), ``"single"`` (treat the string as a single statement), or ``"eval"`` (treat the string as an expression).

Use ``compile()`` when you want to call ``eval()`` or ``exec()`` many times.

In [55]:
compile("y = 2 + 2", "", "exec")

<code object <module> at 0x7ff6284b7d40, file "", line 1>

#### The ``exec()`` Function ####

``eval()`` is for expressions, but ``exec()`` works with suites or even whole programs.

In [56]:
?exec

In [57]:
glob = { 'aGlobalVar': 24 }
loc = { 'aLocalVar': 19 }

print('        before, glob:', glob)
print('                 loc:', loc)

        before, glob: {'aGlobalVar': 24}
                 loc: {'aLocalVar': 19}


In [58]:
stmnt = compile('anotherLocalVar = aGlobalVar + aLocalVar',
                "bogus_file.py", "exec")
stmnt

<code object <module> at 0x7ff6284b75b0, file "bogus_file.py", line 1>

``exec()`` modifies the namespaces passed to it consistently with Python execution.

In [59]:
exec(stmnt, glob, loc)

print('    after, glob keys:', list(glob.keys()))
print('                 loc:', loc)

    after, glob keys: ['aGlobalVar', '__builtins__']
                 loc: {'aLocalVar': 19, 'anotherLocalVar': 43}


And we can uses ``exec()`` to execute whole Python programs from within Python.

In [64]:
pgm = r"""

def main():
    print("Hello, world!")

main()
"""

exec(pgm)

Hello, world!


### Examining Python Bytecodes with the ``dis`` Module

Like most interpreters, Python converts your code into a *bytecode* that is then run by the *virtual machine* (PythonVM). The ``dis`` module lets you look at it.

In [65]:
import dis

allowExceptions = True
if allowExceptions:    
    1/0

ZeroDivisionError: division by zero

Invoking dis.dis() after an exception shows exactly where in the bytecode it occurred.

In [66]:
if allowExceptions:
    dis.dis()

  4           0 LOAD_NAME                0 (allowExceptions)
              2 POP_JUMP_IF_FALSE       12

  5           4 LOAD_CONST               0 (1)
              6 LOAD_CONST               1 (0)
    -->       8 BINARY_TRUE_DIVIDE
             10 POP_TOP
        >>   12 LOAD_CONST               2 (None)
             14 RETURN_VALUE


You can use ``dis.disassemble()`` to show the code of any function.

In [67]:
def fact(n):
    return 1 if n == 0 else n * fact(n-1)

dis.disassemble(fact.__code__)

  2           0 LOAD_FAST                0 (n)
              2 LOAD_CONST               1 (0)
              4 COMPARE_OP               2 (==)
              6 POP_JUMP_IF_FALSE       12
              8 LOAD_CONST               2 (1)
             10 RETURN_VALUE
        >>   12 LOAD_FAST                0 (n)
             14 LOAD_GLOBAL              0 (fact)
             16 LOAD_FAST                0 (n)
             18 LOAD_CONST               2 (1)
             20 BINARY_SUBTRACT
             22 CALL_FUNCTION            1
             24 BINARY_MULTIPLY
             26 RETURN_VALUE


Like assembler, each line is an operation, but there are no registers. The Python VM is *stack-based*.

In [68]:
dis.disassemble(buildMarkovTable.__code__)

  5           0 LOAD_CONST               1 ('\n')
              2 STORE_FAST               1 (nonword)

  7           4 LOAD_FAST                1 (nonword)
              6 STORE_FAST               2 (word1)

  8           8 LOAD_FAST                1 (nonword)
             10 STORE_FAST               3 (word2)

 10          12 BUILD_MAP                0
             14 STORE_FAST               4 (table)

 11          16 LOAD_FAST                0 (words)
             18 GET_ITER
        >>   20 FOR_ITER                60 (to 82)
             22 STORE_FAST               5 (word)

 13          24 LOAD_FAST                2 (word1)
             26 LOAD_FAST                3 (word2)
             28 BUILD_TUPLE              2
             30 LOAD_FAST                4 (table)
             32 COMPARE_OP               6 (in)
             34 POP_JUMP_IF_FALSE       56

 14          36 LOAD_FAST                4 (table)
             38 LOAD_FAST                2 (word1)
             40 LOAD_FA